In [7]:
import pandas as pd
import numpy as np
import hvplot.pandas
import holoviews as hv
import h5py
from PIL import Image

In [8]:
c2_segmented = h5py.File('3pos\pos35\C2_enhanced_Probabilities.h5').get('exported_data')
c3_segmented = h5py.File('3pos\pos35\C3_enhanced_Probabilities.h5').get('exported_data')

In [9]:
c2_segmented.shape

(145, 1, 2048, 2048, 2)

In [10]:
c2_stack_nuclei_prob = c2_segmented[:, 0, ..., 0]
c3_stack_nuclei_prob = c3_segmented[:, 0, ..., 0]

In [5]:
c2_stack_nuclei_prob.shape

(145, 2048, 2048)

In [6]:
hv.Bars([(j, i) for i, j in zip(*np.histogram(c2_stack_nuclei_prob[0, ...]))])

:Bars   [x]   (y)

In [16]:
c2_binary_map = c2_stack_nuclei_prob > 0.8
c3_binary_map = c3_stack_nuclei_prob > 0.8

In [19]:
c2_binary_map.dtype

dtype('bool')

In [11]:
masked_c2 = np.where(c2_stack_nuclei_prob > 0.8, c2_stack_nuclei_prob, 0)
masked_c3 = np.where(c3_stack_nuclei_prob > 0.8, c3_stack_nuclei_prob, 0)

In [13]:
hv.Bars([(j, i) for i, j in zip(*np.histogram(masked_c2[0, ...]))])

:Bars   [x]   (y)

In [20]:
merged_binary_map = np.logical_or(c2_binary_map, c3_binary_map)

In [17]:
with h5py.File('3pos\pos35\merged_binary_map.h5', 'w') as file:
    file.create_dataset('exported_data', data=((masked_c2+masked_c3)/2*255).astype(np.uint8), dtype=np.uint8, chunks=True)

In [16]:
df = df.sort_values(['center_x', 'center_y'])
df['center_x_diff'] = df.center_x.diff()
df['center_y_diff'] = df.center_y.diff()
df['cartesian_distance'] = np.sqrt(df.center_x_diff ** 2 + df.center_y_diff **2)
df


timestep     center_x     center_y  center_x_diff  center_y_diff  \
425          0.0     1.844828   534.931034            NaN            NaN   
720          0.0     2.000000   921.009524       0.155172     386.078489   
1076         0.0     2.125000  1334.083333       0.125000     413.073810   
619          0.0     2.300000   784.962500       0.175000    -549.120833   
265594       0.0     2.408284   965.100592       0.108284     180.138092   
...          ...          ...          ...            ...            ...   
1391         0.0  2045.628571  1753.257143       0.220408    1067.134694   
344          0.0  2045.630435   437.782609       0.001863   -1315.474534   
980          0.0  2045.674419  1222.558140       0.043984     784.775531   
265844       0.0  2045.714286  1892.000000       0.039867     669.441860   
485          0.0  2045.746032   618.507937       0.031746   -1273.492063   

        cartesian_distance  
425                    NaN  
720             386.078521  
1076            413.073828  
619             549.120861  
265594          180.138124  
...                    ...  
1391           1067.134717  
344            1315.474534  
980             784.775532  
265844          669.441862  
485            1273.492064  

[2132 rows x 6 columns]

In [18]:
df.cartesian_distance.describe()

count    2131.000000
mean      624.719395
std       471.935324
min         0.085685
25%       226.733714
50%       540.230692
75%       963.452855
max      1933.633191
Name: cartesian_distance, dtype: float64

In [21]:
df.cartesian_distance.quantile(0.05)

17.684135157405805

In [23]:
c2_image = h5py.File('3pos\pos35\C2_enhanced_Probabilities_uint8.h5').get('exported_data')[0,0,...,0]
c3_image = h5py.File('3pos\pos35\C3_enhanced_Probabilities_uint8.h5').get('exported_data')[0,0,...,0]


In [43]:
merged = c2_image.astype(np.uint16) + c3_image.astype(np.uint16)

cells_df = df.copy().query('cartesian_distance > cartesian_distance.quantile(0.12)')
cells_df.center_x = cells_df.center_x / 2048 - 0.5
cells_df.center_y = -1 * (cells_df.center_y / 2048 - 0.5)

hv.Image(merged.clip(0, 255).astype(np.uint8)).opts(cmap='gray') * cells_df.hvplot.scatter(x='center_x', y='center_y')

:Overlay
   .Image.I   :Image   [x,y]   (z)
   .Scatter.I :Scatter   [center_x]   (center_y)